In [459]:
import requests
from bs4 import BeautifulSoup as bs
import pandas as pd
import datetime
import time
import csv
import numpy as np
import requests
from selenium import webdriver
import pickle
import joblib

In [481]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [464]:
ufc_RF_model = joblib.load('./rfmodel.pkl')

In [439]:
bios = pd.read_csv('UFC_fighter_bios.csv')
bios.drop(columns=['Unnamed: 0'], inplace=True)
bios

fighter    birthday  height  weight  reach       stance
0      Joanna-Jedrzejczyk  1987-08-18    66.0   125.0   65.0     Orthodox
1       Michelle-Waterson  1986-01-06    63.0   115.0   62.0     Orthodox
2             Cub-Swanson  1983-11-02    68.0   145.0   70.0     Orthodox
3             Kron-Gracie  1988-07-11    69.0   145.0   70.0     Southpaw
4              Niko-Price  1989-09-29    72.0   170.0   76.0     Orthodox
5              James-Vick  1987-02-23    75.0   155.0   76.0     Orthodox
6            Amanda-Ribas  1993-08-26    63.0   115.0   66.0     Orthodox
7          Mackenzie-Dern  1993-03-24    64.0   115.0   63.0     Orthodox
8            Matt-Frevola  1990-06-11    69.0   155.0   71.0     Orthodox
9               Luis-Pena  1993-07-05    75.0   155.0   75.0     Southpaw
10            Eryk-Anders  1987-04-21    73.0   205.0   75.0     Southpaw
11     Gerald-Meerschaert  1987-12-18    73.0   185.0   77.0     Southpaw
12             Ryan-Spann  1991-08-24    77.0   205.0   79.0     Orthodox
13            Devin-Clark  1990-04-12    72.0   205.0   75.0     Orthodox
14             Mike-Davis  1992-10-07    72.0   155.0   72.0     Orthodox
15         Thomas-Gifford  1992-07-26    73.0   155.0   75.0     Orthodox
16            Alex-Morono  1990-08-16    71.0   170.0   72.0     Orthodox
17            Max-Griffin  1985-11-29    71.0   170.0   76.0     Orthodox
18    Deiveson-Figueiredo  1987-12-18    65.0   125.0   68.0     Orthodox
19            Tim-Elliott  1986-12-24    67.0   135.0   66.0     Southpaw
20            Marlon-Vera  1992-12-02    68.0   135.0   70.0       Switch
21            Andre-Ewell  1988-01-21    68.0   135.0   75.0     Southpaw
22           Miguel-Baeza  1992-08-23    74.0   170.0   74.0     Orthodox
23          Hector-Aldana  1988-08-17    71.0   170.0   72.0     Orthodox
24         Marvin-Vettori  1993-09-20    72.0   185.0   74.0     Southpaw
25         Andrew-Sanchez  1988-04-08    73.0   185.0   74.0     Orthodox
26             JJ-Aldrich  1992-09-29    65.0   125.0   67.0     Southpaw
27         Lauren-Mueller  1991-11-15    65.0   125.0   67.0     Orthodox
28        Israel-Adesanya  1989-07-22    76.0   185.0   80.0       Switch
29       Robert-Whittaker  1990-12-20    72.0   185.0   73.0     Orthodox
...                   ...         ...     ...     ...    ...          ...
1958          Todd-Medina         NaN    70.0   193.0    NaN     Southpaw
1959       Ernie-Verdicia         NaN    71.0   199.0    NaN     Orthodox
1960             Jon-Hess         NaN    79.0   295.0    NaN          NaN
1961        Andy-Anderson  1974-07-16    66.0   240.0    NaN          NaN
1962           John-Dowdy         NaN     NaN     NaN    NaN          NaN
1963         Asbel-Cancio         NaN    70.0   225.0    NaN          NaN
1964         Melton-Bowen  1969-07-16    72.0   225.0    NaN     Orthodox
1965              Joe-Son  1970-11-22    64.0   236.0    NaN     Orthodox
1966        Ron-van-Clief  1943-01-25    70.0   190.0    NaN     Orthodox
1967          Jason-Fairn         NaN    73.0   230.0    NaN          NaN
1968     Eldo-Xavier-Dias  1964-07-16    71.0   180.0    NaN          NaN
1969         Kevin-Rosier         NaN    76.0   275.0    NaN     Orthodox
1970         Roland-Payne         NaN    69.0   205.0    NaN     Orthodox
1971  Emmanuel-Yarborough  1960-09-05    80.0   770.0    NaN  Open Stance
1972        Johnny-Rhodes         NaN    72.0   210.0    NaN     Orthodox
1973         Orlando-Wiet         NaN    70.0   170.0    NaN     Southpaw
1974          Fred-Ettish         NaN    72.0   180.0    NaN     Southpaw
1975         Scott-Morris         NaN    70.0   210.0    NaN     Orthodox
1976      Minoki-Ichihara         NaN    67.0   178.0    NaN     Orthodox
1977          Scott-Baker         NaN    72.0   210.0    NaN          NaN
1978   Alberta-Cerra-Leon         NaN    68.0   238.0    NaN          NaN
1979     Robert-Lucarelli         NaN    74.0   245.0    NaN          NaN
1980        Frank-Hama

In [440]:
bios['birthday'] = pd.to_datetime(bios['birthday'])

In [441]:
bios_1 = bios.copy()
bios_1['fighter1'] = bios['fighter']
bios_1.drop(columns=['fighter'], inplace=True)

bios_1

birthday  height  weight  reach       stance             fighter1
0    1987-08-18    66.0   125.0   65.0     Orthodox   Joanna-Jedrzejczyk
1    1986-01-06    63.0   115.0   62.0     Orthodox    Michelle-Waterson
2    1983-11-02    68.0   145.0   70.0     Orthodox          Cub-Swanson
3    1988-07-11    69.0   145.0   70.0     Southpaw          Kron-Gracie
4    1989-09-29    72.0   170.0   76.0     Orthodox           Niko-Price
5    1987-02-23    75.0   155.0   76.0     Orthodox           James-Vick
6    1993-08-26    63.0   115.0   66.0     Orthodox         Amanda-Ribas
7    1993-03-24    64.0   115.0   63.0     Orthodox       Mackenzie-Dern
8    1990-06-11    69.0   155.0   71.0     Orthodox         Matt-Frevola
9    1993-07-05    75.0   155.0   75.0     Southpaw            Luis-Pena
10   1987-04-21    73.0   205.0   75.0     Southpaw          Eryk-Anders
11   1987-12-18    73.0   185.0   77.0     Southpaw   Gerald-Meerschaert
12   1991-08-24    77.0   205.0   79.0     Orthodox           Ryan-Spann
13   1990-04-12    72.0   205.0   75.0     Orthodox          Devin-Clark
14   1992-10-07    72.0   155.0   72.0     Orthodox           Mike-Davis
15   1992-07-26    73.0   155.0   75.0     Orthodox       Thomas-Gifford
16   1990-08-16    71.0   170.0   72.0     Orthodox          Alex-Morono
17   1985-11-29    71.0   170.0   76.0     Orthodox          Max-Griffin
18   1987-12-18    65.0   125.0   68.0     Orthodox  Deiveson-Figueiredo
19   1986-12-24    67.0   135.0   66.0     Southpaw          Tim-Elliott
20   1992-12-02    68.0   135.0   70.0       Switch          Marlon-Vera
21   1988-01-21    68.0   135.0   75.0     Southpaw          Andre-Ewell
22   1992-08-23    74.0   170.0   74.0     Orthodox         Miguel-Baeza
23   1988-08-17    71.0   170.0   72.0     Orthodox        Hector-Aldana
24   1993-09-20    72.0   185.0   74.0     Southpaw       Marvin-Vettori
25   1988-04-08    73.0   185.0   74.0     Orthodox       Andrew-Sanchez
26   1992-09-29    65.0   125.0   67.0     Southpaw           JJ-Aldrich
27   1991-11-15    65.0   125.0   67.0     Orthodox       Lauren-Mueller
28   1989-07-22    76.0   185.0   80.0       Switch      Israel-Adesanya
29   1990-12-20    72.0   185.0   73.0     Orthodox     Robert-Whittaker
...         ...     ...     ...    ...          ...                  ...
1958        NaT    70.0   193.0    NaN     Southpaw          Todd-Medina
1959        NaT    71.0   199.0    NaN     Orthodox       Ernie-Verdicia
1960        NaT    79.0   295.0    NaN          NaN             Jon-Hess
1961 1974-07-16    66.0   240.0    NaN          NaN        Andy-Anderson
1962        NaT     NaN     NaN    NaN          NaN           John-Dowdy
1963        NaT    70.0   225.0    NaN          NaN         Asbel-Cancio
1964 1969-07-16    72.0   225.0    NaN     Orthodox         Melton-Bowen
1965 1970-11-22    64.0   236.0    NaN     Orthodox              Joe-Son
1966 1943-01-25    70.0   190.0    NaN     Orthodox        Ron-van-Clief
1967        NaT    73.0   230.0    NaN          NaN          Jason-Fairn
1968 1964-07-16    71.0   180.0    NaN          NaN     Eldo-Xavier-Dias
1969        NaT    76.0   275.0    NaN     Orthodox         Kevin-Rosier
1970        NaT    69.0   205.0    NaN     Orthodox         Roland-Payne
1971 1960-09-05    80.0   770.0    NaN  Open Stance  Emmanuel-Yarborough
1972        NaT    72.0   210.0    NaN     Orthodox        Johnny-Rhodes
1973        NaT    70.0   170.0    NaN     Southpaw         Orlando-Wiet
1974        NaT    72.0   180.0    NaN     Southpaw          Fred-Ettish
1975        NaT    70.0   210.0    NaN     Orthodox         Scott-Morris
1976        NaT    67.0   178.0    NaN     Orthodox      Minoki-Ichihara
1977        NaT    72.0   210.0    NaN          NaN          Scott-Baker
1978        NaT    68.0   238.0    NaN          NaN   Alberta-Cerra-Leon
1979        NaT    74.0   245.0    NaN          NaN     Robert-Lucarelli
1980        NaT     NaN     NaN    NaN          NaN        Frank-

In [442]:
bios_2 = bios.copy()
bios_2['fighter2'] = bios['fighter']
bios_2.drop(columns=['fighter'], inplace=True)

In [443]:
now = pd.Timestamp('now')

In [444]:
newstats = pd.read_csv('newstats.csv')
newstats.drop(columns=['Unnamed: 0'], inplace=True)
newstats

winner                loser      time  \
0      Joanna-Jedrzejczyk    Michelle-Waterson  9.000000   
1             Cub-Swanson          Kron-Gracie  7.000000   
2              Niko-Price           James-Vick  1.733333   
3            Amanda-Ribas       Mackenzie-Dern  7.000000   
4            Matt-Frevola            Luis-Pena  7.000000   
5             Eryk-Anders   Gerald-Meerschaert  7.000000   
6              Ryan-Spann          Devin-Clark  3.016667   
7              Mike-Davis       Thomas-Gifford  6.750000   
8             Alex-Morono          Max-Griffin  7.000000   
9     Deiveson-Figueiredo          Tim-Elliott  3.133333   
10            Marlon-Vera          Andre-Ewell  5.283333   
11           Miguel-Baeza        Hector-Aldana  3.533333   
12         Marvin-Vettori       Andrew-Sanchez  7.000000   
13             JJ-Aldrich       Lauren-Mueller  7.000000   
14        Israel-Adesanya     Robert-Whittaker  4.550000   
15             Dan-Hooker          Al-Iaquinta  7.000000   
16         Serghei-Spivac          Tai-Tuivasa  4.233333   
17            Dhiego-Lima          Luke-Jumeau  7.000000   
18       Yorgan-De-Castro          Justin-Tafa  2.166667   
19          Jake-Matthews         Rostem-Akman  7.000000   
20          Callan-Potter          Maki-Pitolo  7.000000   
21           Brad-Riddell      Jamie-Mullarkey  7.000000   
22         Megan-Anderson          Zarah-Fairn  3.950000   
23            Ji-Yeon-Kim         Nadia-Kassem  5.983333   
24            Khalid-Taha          Bruno-Silva  5.000000   
25        Jared-Cannonier      Jack-Hermansson  1.450000   
26            Mark-Madsen     Danilo-Belluardo  1.200000   
27          Gilbert-Burns        Gunnar-Nelson  7.000000   
28           Ion-Cutelaba  Khalil-Rountree-Jr.  2.583333   
29     Ovince-Saint-Preux  Michal-Oleksiejczuk  3.766667   
...                   ...                  ...       ...   
4736           Luke-Cummo       Jason-Von-Flue  7.000000   
4737            Jon-Fitch       Joshua-Burkman  5.950000   
4738       Dan-Christison            Brad-Imes  5.616667   
4739        Josh-Koscheck      Ansar-Chalangov  3.483333   
4740         Chael-Sonnen      Trevor-Prangley  7.000000   
4741        Rich-Franklin        David-Loiseau  9.000000   
4742           Mike-Swick      Steve-Vigneault  2.150000   
4743    Georges-St-Pierre              BJ-Penn  7.000000   
4744       Nate-Marquardt         Joe-Doerksen  7.000000   
4745        Mark-Hominick         Yves-Edwards  2.866667   
4746            Sam-Stout       Spencer-Fisher  7.000000   
4747        Jason-Lambert        Rob-MacDonald  1.900000   
4748           Tom-Murphy         Icho-Larenas  3.983333   
4749        Chuck-Liddell        Randy-Couture  2.466667   
4750         Brandon-Vera        Justin-Eilers  1.416667   
4751          Marcio-Cruz            Frank-Mir  4.166667   
4752        Renato-Sobral     Mike-van-Arsdale  2.350000   
4753            Joe-Riggs            Nick-Diaz  7.000000   
4754       Alessio-Sakara        Elvis-Sinosic  7.000000   
4755       Paul-Buentello       Gilbert-Aldana  3.450000   
4756          Jeff-Monson   Branden-Lee-Hinkle  4.583333   
4757        Keith-Jardine       Mike-Whitehead  7.000000   
4758           Tim-Sylvia       Assuerio-Silva  7.000000   
4759       Stephan-Bonnar          James-Irvin  4.500000   
4760       Joshua-Burkman         Drew-Fickett  1.116667   
4761          Chris-Leben         Jorge-Rivera  1.733333   
4762            Josh-Neer      Melvin-Guillard  4.333333   
4763         Duane-Ludwig      Jonathan-Goulet  0.183333   
4764       Spencer-Fisher          Aaron-Riley  5.000000   
4765       Jason-Von-Flue       Alex-Karalexis  3.283333   

                weightclass                  method  \
0       Women's Strawweight                   U-DEC   
1             Featherweight                   U-DEC   
2              Welterweight            KO/TKO  Kick   
3       Women's Strawweight                   U-DEC   
4               Lightwe

In [486]:
tobestand = pd.read_csv('realmodeldf.csv')

tobestand.drop(columns=['Unnamed: 0', 'fight', 'date', 'fighter_1', 'fighter_2', 'winner'], inplace=True)
tobestand

cumultime_1  cumulStr_Att_fighter_1  cumulStr_Att_oponent_1  \
0       97.650000                  2153.0                  1614.0   
1       16.016667                   138.0                   138.0   
2       11.533333                   181.0                   213.0   
3       78.383333                   872.0                   434.0   
4       15.283333                   187.0                   237.0   
5       59.650000                   939.0                   673.0   
6      106.533333                  1271.0                  1247.0   
7       14.883333                   333.0                   245.0   
8        9.466667                    92.0                   118.0   
9       65.983333                   897.0                  1050.0   
10      41.050000                   684.0                   499.0   
11      23.200000                   748.0                   526.0   
12      23.633333                   266.0                   331.0   
13      15.100000                   344.0                   209.0   
14      17.950000                   319.0                   337.0   
15      48.000000                   911.0                   689.0   
16       8.100000                   123.0                   153.0   
17      32.566667                   346.0                   529.0   
18      65.650000                   840.0                   638.0   
19      51.316667                   807.0                   534.0   
20      31.983333                   606.0                   604.0   
21      27.700000                   246.0                   369.0   
22      45.916667                   484.0                   543.0   
23      30.783333                   501.0                   438.0   
24      48.566667                   502.0                   626.0   
25      26.900000                   712.0                   537.0   
26      41.350000                   684.0                   533.0   
27      59.383333                   853.0                   451.0   
28      22.833333                   165.0                   160.0   
29      22.300000                   222.0                   248.0   
30      12.583333                    63.0                   202.0   
31      34.516667                   492.0                   467.0   
32      22.016667                   200.0                   245.0   
33       5.350000                    50.0                    57.0   
34     103.916667                  1116.0                  1248.0   
35      15.416667                   198.0                   154.0   
36      64.166667                   854.0                   460.0   
37      49.033333                   917.0                  1007.0   
38      32.466667                   251.0                   258.0   
39      52.916667                   575.0                   610.0   
40      67.166667                  1020.0                  1252.0   
41      14.000000                   177.0                   281.0   
42      42.000000                  1433.0                  1370.0   
43      39.000000                   456.0                   494.0   
44      49.300000                   604.0                   611.0   
45      64.833333                   917.0                   827.0   
46      10.816667                   129.0                   163.0   
47      25.933333                   290.0                   374.0   
48      42.283333                   780.0                   696.0   
49     117.100000                  1414.0                  1328.0   
50      48.283333                   396.0                   532.0   
51      16.383333                    98.0                   151.0   
52      91.350000                  1175.0                  1111.0   
53      27.750000                   595.0                   737.0   
54      23.783333                   475.0                   509.0   
55      28.766667                   471.0                   501.0   
56      29.200000                   480.0                   374.0   
57  

In [445]:
def get_cumul_fighter_dfs(fighter):
    

    fighter_L = newstats[newstats['loser']==fighter][['date', 'time',
                                                  'winner', 'loser',
                                                  'Str_Att_l', 'TD_Att_l',
                                                  'Str_Att_w', 'TD_Att_w',
                                                  'KDpm_l', 'KDpm_ratio_l', 
                                                  'SLPM_l', 'SLPMratio_l', 'SAPM_l', 'SAPM_ratio_l',
                                                  'Str_Acc_l', 'Str_Acc_ratio_l', 'Str_Def_l',
                                                  'TDPM_l', 'TD_Acc_l', 'TD_Def_l', 'SubPM_l', 'PassPM_l',
                                                  'RevPM_l', 'Head_SLPM_l', 'Body_SLPM_l', 'Leg_SLPM_l',
                                                  'Dist_SLPM_l', 'Clinch_SLPM_l', 'Ground_SLPM_l']]
    
    fighter_W = newstats[newstats['winner']==fighter][['date', 'time',
                                                  'winner', 'loser',        
                                                  'Str_Att_w', 'TD_Att_w',
                                                  'Str_Att_l', 'TD_Att_l',
                                                  'KDpm_w', 'KDpm_ratio_w', 
                                                  'SLPM_w', 'SLPMratio_w', 'SAPM_w', 'SAPM_ratio_w',
                                                  'Str_Acc_w', 'Str_Acc_ratio_w', 'Str_Def_w',
                                                  'TDPM_w', 'TD_Acc_w', 'TD_Def_w', 'SubPM_w', 'PassPM_w',
                                                  'RevPM_w', 'Head_SLPM_w', 'Body_SLPM_w', 'Leg_SLPM_w',
                                                  'Dist_SLPM_w', 'Clinch_SLPM_w', 'Ground_SLPM_w']]
    
    
    
    fighter_W = fighter_W.rename(columns={'Str_Att_w': 'Str_Att_fighter', 'Str_Att_l':'Str_Att_opponent',
                            'TD_Att_w': 'TD_Att_fighter', 'TD_Att_l': 'TD_Att_opponent',
                            'KDpm_w': 'KDpm', 'KDpm_ratio_w': 'KDpm_ratio', 'SLPM_w': 'SLPM',
                            'SLPMratio_w': 'SLPM_ratio', 'SAPM_w': 'SAPM', 'SAPM_ratio_w': 'SAPM_ratio',
                            'Str_Acc_w': 'Str_Acc', 'Str_Acc_ratio_w': 'Str_Acc_ratio', 'Str_Def_w': 'Str_Def',
                            'TDPM_w': 'TDPM', 'TD_Acc_w': 'TD_Acc', 'TD_Def_w': 'TD_Def', 'SubPM_w': 'SubPM',
                            'PassPM_w': 'PassPM', 'RevPM_w': 'RevPM', 'Head_SLPM_w': 'Head_SLPM',
                            'Body_SLPM_w': 'Body_SLPM', 'Leg_SLPM_w': 'Leg_SLPM', 'Dist_SLPM_w': 'Dist_SLPM',
                            'Clinch_SLPM_w': 'Clinch_SLPM', 'Ground_SLPM_w': 'Ground_SLPM'})

    fighter_L = fighter_L.rename(columns={'Str_Att_l': 'Str_Att_fighter', 'Str_Att_w':'Str_Att_opponent',
                            'TD_Att_l': 'TD_Att_fighter', 'TD_Att_w': 'TD_Att_opponent',
                            'KDpm_l': 'KDpm', 'KDpm_ratio_l': 'KDpm_ratio', 'SLPM_l': 'SLPM',
                            'SLPMratio_l': 'SLPM_ratio', 'SAPM_l': 'SAPM', 'SAPM_ratio_l': 'SAPM_ratio',
                            'Str_Acc_l': 'Str_Acc', 'Str_Acc_ratio_l': 'Str_Acc_ratio', 'Str_Def_l': 'Str_Def',
                            'TDPM_l': 'TDPM', 'TD_Acc_l': 'TD_Acc', 'TD_Def_l': 'TD_Def', 'SubPM_l': 'SubPM',
                            'PassPM_l': 'PassPM', 'RevPM_l': 'RevPM', 'Head_SLPM_l': 'Head_SLPM',
                            'Body_SLPM_l': 'Body_SLPM', 'Leg_SLPM_l': 'Leg_SLPM', 'Dist_SLPM_l': 'Dist_SLPM',
                            'Clinch_SLPM_l': 'Clinch_SLPM', 'Ground_SLPM_l': 'Ground_SLPM'})
    
    
    
    
    
    
    fighter_df = fighter_W.append(fighter_L)
    fighter_df = fighter_df.sort_values(by='date')
    
    
    
    
    cumul_df = pd.DataFrame()
    
    
    
    cumul_df['winner'] = list(fighter_df['winner']) + ['']
    cumul_df['loser'] = list(fighter_df['loser']) + ['']
    cumul_df['date'] = list(fighter_df['date']) + ['']
    cumul_df['cumultime'] = [0] + list(np.cumsum(list(fighter_df['time'])))
    cumul_df['cumulStr_Att_fighter'] = [0] + list(np.cumsum(list(fighter_df['Str_Att_fighter'])))
    cumul_df['cumulStr_Att_oponent'] = [0] + list(np.cumsum(list(fighter_df['Str_Att_opponent'])))
    cumul_df['cumulTD_Att_fighter'] = [0] + list(np.cumsum(list(fighter_df['TD_Att_fighter'])))
    cumul_df['cumulTD_Att_oponent'] = [0] + list(np.cumsum(list(fighter_df['TD_Att_opponent'])))

    
    cumulKDPM = [0]
    cumulKDPM_ratio = [0]
    cumulSLPM = [0]
    cumulSLPM_ratio = [0]
    cumulSAPM = [0]
    cumulSAPM_ratio = [0]
    cumulStr_Acc = [0]
    cumulStr_Def = [0]
    cumulTD_Acc = [0]
    cumulTD_Def = [0]
    cumulSubPM = [0]
    cumulPassPM = [0]
    cumulRevPM = [0]
    cumulHead_SLPM = [0]
    cumulBody_SLPM = [0]
    cumulLeg_SLPM = [0]
    cumulDist_SLPM = [0]
    cumulClinch_SLPM = [0]
    cumulGround_SLPM = [0]


    for i in range(len(cumul_df)-1):
        cumulKDPM.append((list(np.cumsum(list(fighter_df['KDpm']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulKDPM_ratio.append((list(np.cumsum(list(fighter_df['KDpm_ratio']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulSLPM.append((list(np.cumsum(list(fighter_df['SLPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulSLPM_ratio.append((list(np.cumsum(list(fighter_df['SLPM_ratio']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulSAPM.append((list(np.cumsum(list(fighter_df['SAPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulSAPM_ratio.append((list(np.cumsum(list(fighter_df['SAPM_ratio']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulStr_Acc.append((list(np.cumsum(list(fighter_df['Str_Acc']))))[i] / (list(np.cumsum(list(fighter_df['Str_Att_fighter']))))[i])
        cumulStr_Def.append((list(np.cumsum(list(fighter_df['Str_Def']))))[i] / (list(np.cumsum(list(fighter_df['Str_Att_opponent']))))[i])
        cumulTD_Acc.append((list(np.cumsum(list(fighter_df['TD_Acc']))))[i] / (list(np.cumsum(list(fighter_df['TD_Att_fighter']))))[i])
        cumulTD_Def.append((list(np.cumsum(list(fighter_df['TD_Def']))))[i] / (list(np.cumsum(list(fighter_df['TD_Att_opponent']))))[i])
        cumulSubPM.append((list(np.cumsum(list(fighter_df['SubPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])    
        cumulPassPM.append((list(np.cumsum(list(fighter_df['PassPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulRevPM.append((list(np.cumsum(list(fighter_df['RevPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulHead_SLPM.append((list(np.cumsum(list(fighter_df['Head_SLPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulBody_SLPM.append((list(np.cumsum(list(fighter_df['Body_SLPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulLeg_SLPM.append((list(np.cumsum(list(fighter_df['Leg_SLPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulDist_SLPM.append((list(np.cumsum(list(fighter_df['Dist_SLPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulClinch_SLPM.append((list(np.cumsum(list(fighter_df['Clinch_SLPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        cumulGround_SLPM.append((list(np.cumsum(list(fighter_df['Ground_SLPM']))))[i] / (list(np.cumsum(list(fighter_df['time']))))[i])
        

    

    cumul_df['KDPM'] = cumulKDPM
    cumul_df['KDPM_ratio'] = cumulKDPM_ratio
    cumul_df['SLPM'] = cumulSLPM
    cumul_df['SLPM_ratio'] = cumulSLPM_ratio
    cumul_df['SAPM'] = cumulSAPM
    cumul_df['SAPM_ratio'] = cumulSAPM_ratio
    cumul_df['Str_Acc'] = cumulStr_Acc
    cumul_df['Str_Def'] = cumulStr_Def
    cumul_df['TD_Acc'] = cumulTD_Acc
    cumul_df['TD_Def'] = cumulTD_Def
    cumul_df['SubPM'] = cumulSubPM
    cumul_df['PassPM'] = cumulPassPM
    cumul_df['RevPM'] = cumulRevPM
    cumul_df['Head_SLPM'] = cumulHead_SLPM
    cumul_df['Body_SLPM'] = cumulBody_SLPM
    cumul_df['Leg_SLPM'] = cumulLeg_SLPM
    cumul_df['Dist_SLPM'] = cumulDist_SLPM
    cumul_df['Clinch_SLPM'] = cumulClinch_SLPM
    cumul_df['Ground_SLPM'] = cumulGround_SLPM
    
    
    win = 0
    loss = 0
    wins = [0]
    losses = [0]
    for i in range(len(cumul_df)-1):

        if cumul_df['winner'][i]==fighter:
            win+=1
            wins.append(win)
            losses.append(loss)
        else:
            loss+=1
            losses.append(loss)
            wins.append(win)
    
    cumul_df['wins'] = wins
    cumul_df['losses'] = losses
    
    return cumul_df
    
    

In [514]:
def get_new_picks(eventoddsURL):



    org = pd.concat(pd.read_html(eventoddsURL)[8::3])
    new = pd.DataFrame()
    new['fighters'] = list(org[1][:-1:2])
    new['odd1'] = list(org[0][1::2])
    new['odd2'] = list(org[2][1::2])
    newf = []
    for i in list(new['fighters']):
        newf.append(i.split(' Fight Weight')[0])

    fig1 = []
    fig2 = []
    for i in newf:
        fig1.append(i.split(' vs ')[0])
        fig2.append(i.split(' vs ')[1])

    figh1 = []
    for i in fig1:
        figh1.append(i.replace(' ', '-'))
    figh2 = []
    for i in fig2:
        figh2.append(i.replace(' ', '-'))

    odd1 = []
    for i in list(new['odd1']):
        odd1.append(float(i.replace('@','')))
    odd2 = []
    for i in list(new['odd2']):
        odd2.append(float(i.replace('@','')))
    implied_prob_1 = []
    for i in odd1:
        implied_prob_1.append(1/i)
    implied_prob_2 = []
    for i in odd2:
        implied_prob_2.append(1/i)    
    
    newodds = pd.DataFrame()
    newodds['fighter1'] = figh1
    newodds['fighter2'] = figh2
    newodds['implied_prob_1'] = implied_prob_1
    newodds['implied_prob_2'] = implied_prob_2
    
    #above is getting gambling odds and names of fighters
    #below is getting stats for thos fighters and combining that with the odds
    
    fights = list(zip(figh1, figh1))
    
    f1=[]
    f2=[]
    for i in fights:
        f1.append(get_cumul_fighter_dfs(i[0]))
        f2.append(get_cumul_fighter_dfs(i[1]))
    
    fighter1 = []
    fighter2 = []
    for i in range(len(f1)):
        fighter1.append(pd.DataFrame(f1[i].iloc[-1]).T)
        fighter2.append(pd.DataFrame(f2[i].iloc[-1]).T)

    df1 = pd.concat(fighter1)
    df2 = pd.concat(fighter2)
    
    df1['fighter1'] = figh1
    df1['fighter2'] = figh2
    df2['fighter1'] = figh1
    df2['fighter2'] = figh2    

    
    df1 = pd.merge(df1, bios_1, how='inner', on='fighter1')
    df2 = pd.merge(df2, bios_2, how='inner', on='fighter2')
    
    
    df1['prev'] = df1['wins'] = df1['losses']
    df2['prev'] = df2['wins'] = df2['losses']
    
    df1 = pd.get_dummies(data=df1, columns=['stance'])
    df2 = pd.get_dummies(data=df2, columns=['stance'])
    
    df1 = df1.add_suffix('_1')
    df2 = df2.add_suffix('_2')

    
    df1.drop(columns=['winner_1','loser_1', 'date_1'], inplace=True)
    df2.drop(columns=['winner_2','loser_2', 'date_2'], inplace=True)
    
    df1.rename(columns={'fighter1_1': 'fighter1', 'fighter2_1': 'fighter2'}, inplace=True)
    df2.rename(columns={'fighter1_2': 'fighter1', 'fighter2_2': 'fighter2'}, inplace=True)
    
    df1['age_1'] = (now - df1['birthday_1']).astype('<m8[Y]')
    df2['age_2'] = (now - df2['birthday_2']).astype('<m8[Y]')
    

    cumulstats_bios = pd.merge(df1, df2, how='inner', on=['fighter1', 'fighter2'])
    
    cumulstats_bios = pd.merge(cumulstats_bios, newodds, how='inner', on=['fighter1', 'fighter2'])
    
#     .drop(columns=['fighter1', 'fighter2'])
    ## might want to drop these columns but will leave them in so I know what fight is what
    
    
    cumulstats_bios.drop(columns=['birthday_1', 'birthday_2'], inplace=True)
    
    #making sure I only get fights where both fighters have fought 2+ fights and 3+ mins
    cumulstats_bios = cumulstats_bios.loc[cumulstats_bios['prev_1'] >= 2]
    cumulstats_bios = cumulstats_bios.loc[cumulstats_bios['prev_2'] >= 2]
    
    cumulstats_bios = cumulstats_bios.loc[cumulstats_bios['cumultime_1'] >= 3]
    cumulstats_bios = cumulstats_bios.loc[cumulstats_bios['cumultime_2'] >= 3]
    
    cumulstats_bios.fillna(0, inplace=True)
    
    
    
    this_week_fights = pd.DataFrame()
    this_week_fights['fighter1'] = cumulstats_bios['fighter1']
    this_week_fights['fighter2'] = cumulstats_bios['fighter2']
    this_week_fights['vegas_prob_1'] = cumulstats_bios['implied_prob_1']
    this_week_fights['vegas_prob_2'] = cumulstats_bios['implied_prob_2']
    this_week_fights['vegas_payout_1'] = list((1/i) for i in list(cumulstats_bios['implied_prob_1']))
    this_week_fights['vegas_payout_2'] = list((1/i) for i in list(cumulstats_bios['implied_prob_2']))
    
    thisweek_predict = cumulstats_bios.drop(columns=['fighter1','fighter2'])
    
    
    
    appendednew = tobestand.append(thisweek_predict)
    appendednew.fillna(0, inplace=True)
    
    for col in appendednew.columns:
        appendednew[col] = (appendednew[col]-min(appendednew[col])) / (max(appendednew[col]) - min(appendednew[col])) #subtract the minimum and divide by the range forcing a scale of 0 to 1 for each feature
      
    test_thisweek = appendednew[-len(thisweek_predict):]
#     test_thisweek = appendednew[-5:]
    
    tw_myprob_1 = list(pd.DataFrame(ufc_RF_model.predict_proba(test_thisweek))[0])
    tw_myprob_2 = list(pd.DataFrame(ufc_RF_model.predict_proba(test_thisweek))[1])
    
    this_week_fights['my_prob_1'] = tw_myprob_1
    this_week_fights['my_prob_2'] = tw_myprob_2
    this_week_fights['my_payout_1'] = list((1/i) for i in list(this_week_fights['my_prob_1']))
    this_week_fights['my_payout_2'] = list((1/i) for i in list(this_week_fights['my_prob_2']))
    
    thisweektakes_1 = this_week_fights[this_week_fights['my_payout_1'] < this_week_fights['vegas_payout_1']*.9]
    thisweektakes_2 = this_week_fights[this_week_fights['my_payout_2'] < this_week_fights['vegas_payout_2']*.9]
    thisweektakes_1['mytake'] = 1
    thisweektakes_2['mytake'] = 2
    
    thisweekstakes = thisweektakes_1.append(thisweektakes_2)
        
    return thisweekstakes 



In [515]:
UFC_Fight_Night_162 = 'https://www.betmma.tips/UFC_event_stats.php?Event=536'

In [516]:
get_new_picks(UFC_Fight_Night_162)

/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:103: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:104: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:103: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:104: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:103: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:103: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:104: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnath

fighter1        fighter2  vegas_prob_1  vegas_prob_2  \
1    Frank-Camacho  Beneil-Dariush      0.420168      0.602410   
5  Enrique-Barzola   Movsar-Evloev      0.384615      0.632911   
7       Alex-White   Rafael-Fiziev      0.363636      0.649351   
3  Michael-Johnson      Stevie-Ray      0.724638      0.277778   

   vegas_payout_1  vegas_payout_2  my_prob_1  my_prob_2  my_payout_1  \
1            2.38            1.66   0.558755   0.441245     1.789692   
5            2.60            1.58   0.453408   0.546592     2.205519   
7            2.75            1.54   0.592962   0.407038     1.686449   
3            1.38            3.60   0.600577   0.399423     1.665065   

   my_payout_2  mytake  
1     2.266317       1  
5     1.829518       1  
7     2.456772       1  
3     2.503613       2

In [517]:
UFC_244 = 'https://www.betmma.tips/UFC_event_stats.php?Event=526'

In [518]:
get_new_picks(UFC_244)

/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:104: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:104: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:103: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:104: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:103: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:104: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnathel/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:103: RuntimeWarning: invalid value encountered in double_scalars
/Users/hmnath

fighter1         fighter2  vegas_prob_1  vegas_prob_2  \
1     Corey-Anderson    Johnny-Walker      0.403226      0.598802   
2        Darren-Till  Kelvin-Gastelum      0.395257      0.617284   
3      Derrick-Lewis    Blagoy-Ivanov      0.473934      0.540541   
4   Stephen-Thompson    Vicente-Luque      0.546448      0.458716   
7  Katlyn-Chookagian    Jennifer-Maia      0.598802      0.416667   

   vegas_payout_1  vegas_payout_2  my_prob_1  my_prob_2  my_payout_1  \
1            2.48            1.67   0.456772   0.543228     2.189277   
2            2.53            1.62   0.538374   0.461626     1.857446   
3            2.11            1.85   0.578793   0.421207     1.727733   
4            1.83            2.18   0.420921   0.579079     2.375745   
7            1.67            2.40   0.369636   0.630364     2.705364   

   my_payout_2  mytake  
1     1.840847       1  
2     2.166255       1  
3     2.374131       1  
4     1.726879       2  
7     1.586385       2

In [503]:
get_new_picks('https://www.betmma.tips/UFC_event_stats.php?Event=537')
#odds not out yet for these fights

ZeroDivisionError: float division by zero